# Final Project

In [ ]:
import numpy as np
%matplotlib osx
import matplotlib.pyplot as plt
length = np.linalg.norm

In [ ]:
def normalize(v):
    l = length(v)
    if length(v) == 0:
        return v[:]
    return v / length(v)

def project(a, b):
    bn = normalize(b)
    return np.dot(a, bn) * bn

In [ ]:
class Ray:
    def __init__(self, start, dir):
        self.dir = normalize(np.array(dir))
        self.pos = np.array(start)
        self.exclude = None
        
    def step(self, objects):
        closestObj = None;
        closestDist = 1e10
        # find the closest object
        for obj in objects:
            if obj == self.exclude:
                continue
            dist = obj.distance(self)
            if (dist < closestDist):
                closestDist = dist
                closestObj = obj

        returnLine = Line(self.pos, self.pos + self.dir * closestDist)
        self.exclude = closestObj
        self.pos = returnLine.end
        if (closestObj):
            self.dir = closestObj.newRay()
        return returnLine

class Line:
    def __init__(self, start, end):
        start = np.array(start)
        end = np.array(end)
        
        self.start = start
        self.end = end
        self.dir = normalize(self.end - self.start)
        self.length = length(start - end)

    def distFrom(self, pos):
        vLine = self.end - self.start
        vPos = pos - self.start
        proj = np.dot(vPos, self.dir)
        proj = np.clip(proj, 0, self.length)
        return length(vPos - proj * self.dir)

In [ ]:
def drawLine(line, img):
    w = img.shape[0]
    h = img.shape[1]

    pos = np.copy(line.start) * img.shape;
    floorPos = np.floor(pos).astype(int)
    while True:
        toMiddle = np.array(img.shape) / 2 - pos
        if np.dot(toMiddle, toMiddle) > img.shape[0] * img.shape[1] / 2 and np.dot(toMiddle, line.dir) < 0:
            break
        
        if not (0 <= pos[0] < w and 0 <= pos[1] < h):
            pos += line.dir
            floorPos = np.floor(pos).astype(int)
            continue
            
        tPos = pos - floorPos
        tDir = line.dir.copy()
        # print(1, tPos, tDir)
        if (tDir[0] < 0):
            tDir[0] *= -1
            tPos[0] = 1 - tPos[0]
        if (tDir[1] < 0):
            tDir[1] *= -1
            tPos[1] = 1 - tPos[1]
        # print(2, tPos, tDir)
        tPos = np.mod(tPos, 1)
        # x=1 line
        if tDir[0] == 0:
            y1 = 2
        else:
            y1 = tDir[1]/tDir[0] * (1 - tPos[0]) + tPos[1]

        #y=1 line
        if tDir[1] == 0:
            x1 = 2
        else:
            x1 = tDir[0]/tDir[1] * (1 - tPos[1]) + tPos[0]

        pX1 = np.array([1, y1])
        pY1 = np.array([x1, 1])
        distX1 = length(pX1 - tPos)
        distY1 = length(pY1 - tPos)

        # print(3, tPos, tDir)
        if distX1 < distY1:
            img[floorPos[0], floorPos[1]] += distX1;
            floorPos[0] += np.sign(line.dir[0])
            pos[0] = floorPos[0]
            pos[1] += line.dir[1] * distX1
        elif distY1 < distX1:
            img[floorPos[0], floorPos[1]] += distY1;
            floorPos[1] += np.sign(line.dir[1])
            pos[1] = floorPos[1]
            pos[0] += line.dir[0] * distY1
        else:
            floorPos[0] += np.sign(line.dir[0])
            floorPos[1] += np.sign(line.dir[1])
            pos = floorPos.copy()

        if length(pos / img.shape - line.start) > line.length:
            break

In [ ]:
def drawLineFast(line, img):
    w = img.shape[0]
    h = img.shape[1]
    pos = np.copy(line.start) * img.shape;
    while True:
        toMiddle = np.array(img.shape) / 2 - pos
        if np.dot(toMiddle, toMiddle) > img.shape[0] * img.shape[1] / 2 and np.dot(toMiddle, line.dir) < 0:
            break
        
        if not (0 <= pos[0] < w and 0 <= pos[1] < h):
            pos += line.dir
            continue
        
        floorPos = np.floor(pos).astype(int)
        img[floorPos[0], floorPos[1]] += 1
        pos += line.dir
        if length(pos / img.shape - line.start) > line.length:
            break

In [ ]:
# img = np.zeros((10,10))
# drawLineFast(Line([0.5, -5], [0.6, 1e10]), img)
# plt.imshow(img.T)

In [ ]:
class Lens():
    def __init__(self, pos, dir, focalLength):
        self.pos = np.array(pos)
        
        self.dir = np.array(dir)
        
        self.focalLength = focalLength

        self.p1 = self.pos + np.array([self.dir[1], -self.dir[0]])
        self.p2 = self.pos + np.array([-self.dir[1], self.dir[0]])

    def distance(self, ray):

 
        # check if touching https://stackoverflow.com/questions/13640931/how-to-determine-if-a-vector-is-between-two-other-vectors
        dp1 = self.p1 - ray.pos
        dp2 = self.p2 - ray.pos
        if not (np.cross(dp1, ray.dir) * np.cross(dp1, dp2) >= 0 and np.cross(dp2, ray.dir) * np.cross(dp2, dp1) >= 0):
            return 1e10

        d = ray.pos - self.p1
        projection = self.p1 + project(d, self.p1 - self.p2)
        ortho = projection - ray.pos

        dist = length(ortho) / np.dot(normalize(ortho), normalize(ray.dir))
        if (dist < 0):
            return 1e10

        self.initialPos = ray.pos.copy()
        self.ray = ray
        return dist
        
    def newRay(self):
        normalDir = normalize(self.dir)
        vo = self.initialPos - self.pos
        do = np.dot(vo, normalDir)
        ho = vo - do * normalDir

        do = abs(do)
        di = 1 / (1 / self.focalLength - 1 / do)
        hi = - ho * di / do

        vi = hi - normalDir * di * np.sign(np.dot(vo, normalDir))
        
        newDir = normalize(self.pos + vi - self.ray.pos)
        return newDir * np.sign(np.dot(newDir, - normalDir * np.sign(np.dot(normalDir, vo))))

    def draw(self, img):
        a = np.max(img)
        for i in range(img.shape[0]):
            y = i / img.shape[0]
            for j in range(img.shape[1]):
                x = j / img.shape[1]
                l = Line(self.p1, self.p2)
                pos = np.array([x, y])
                d = l.distFrom(pos)
                if d < 0.005:
                    img[i, j] = a
                elif d < 0.01:
                    img[i, j] = a * (0.01 - d)

In [ ]:
class Mirror(Lens):
    def newRay(self):
        normalDir = normalize(self.dir)
        vo = self.initialPos - self.pos
        do = np.dot(vo, normalDir)
        ho = vo - do * normalDir

        do = abs(do)
        di = 1 / (1 / self.focalLength - 1 / do)
        hi = ho * di / do

        vi = hi - normalDir * di * np.sign(np.dot(vo, normalDir))
        
        newDir = normalize(self.pos + vi - self.ray.pos)
        return newDir * np.sign(np.dot(newDir, normalDir * np.sign(np.dot(normalDir, vo))))

In [ ]:
def createImage(rayPos, objects, resolution, numRays):
    img = np.zeros((resolution, resolution))
    offsets = {}
    for i in range(numRays):
        #theta = np.random.random() * 2 * np.pi
        theta = i / numRays * 2 * np.pi
        if i not in offsets:
            offsets[i] = (np.random.rand((2)) - 0.5) * 0.001
        r = Ray(rayPos + offsets[i], [np.sin(theta), np.cos(theta)])
        while True:
            line = r.step(objects)
            drawLine(line, img)
            if length(line.end) > 1e5:
                break

    # postproecessing
    img = img.T
    img = 1 - np.exp(-img / np.average(img) * 0.2)
    for obj in objects:
        obj.draw(img)

    return img

In [ ]:
def mv(v, t):
    v = np.array(v)
    return v + normalize(v - np.array([0.5, 0.5])) * np.exp(-t*0.1) * 0.5

In [ ]:
# for t in range(10):
#     objects = [Lens(mv([0.5, 0.5], t), [0.1, 0], 0.2), Mirror(mv([0.2, 0.3], t + 1), [0.05, 0.05], 1)]
#     rayPos = [0.8, 0.7]
    
#     plt.imshow(createImage(rayPos, objects, 80, 1000))
#     plt.pause(0.1)

objects = [
    Lens([0.85, 0.15], [-0.1, 0.1], 0.046),
    Lens([0.8, 0.2], [-0.05, 0.05], -0.06),
    Mirror([0.7, 0.35], [0.05, 0], 0.06),
    Mirror([0.65, 0.3], [0, 0.05], 0.06),
    Mirror([0.8, 0.45], [0.05, 0], 0.06),
    Mirror([0.55, 0.2], [0, 0.05], 0.06),
    Lens([0.55, 0.45], [-0.15, 0.15], 0.1),
    Lens([0.4, 0.6], [-0.15, 0.15], --0.09),
    Mirror([0.15, 0.85], [-0.05, 0.05], --0.09),
]

rayPos = [0.9, 0.1]
# plt.imshow(createImage(rayPos, objects, 100, 1000))

In [ ]:
" add rays "
# img = np.zeros((400, 400))
# objects = [Lens([0.5, 0.5], [0.1, 0], 0.1), Mirror([0.2, 0.5], [0.1, 0], 0.08)]
# r = Ray([0.9, 0.7], [-1.501, -1])

# from matplotlib.animation import FFMpegWriter
# metadata = dict(title='idk', artist='Me',comment='hi.')
# writer = FFMpegWriter(fps=15, metadata=metadata)

# fig = plt.figure()
# with writer.saving(fig, "addRays.mp4", dpi=200):
#     nf = 100
#     for it in range(nf):
#         if (it%10==0): print(it,end='')
#         print('.',end='')

#         n = 50

#         plt.clf()
#         plt.imshow(createImage([0.9, 0.7], objects, 400, np.floor(np.exp(it * 0.0860323)).astype(int)))
#         plt.show()
#         plt.draw()
        
#         plt.pause(0.05)
#         writer.grab_frame()

In [ ]:
""" star """
# from matplotlib.animation import FFMpegWriter
# metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
# writer = FFMpegWriter(fps=15, metadata=metadata)

# fig = plt.figure()
# with writer.saving(fig, "FinalTest.mp4", dpi=200):
#     nf = 140
#     for it in range(nf):
#         if (it%10==0): print(it,end='')
#         print('.',end='')

#         n = 50
        
#         objects = [
#             Lens(mv([0.292, 0.9], it), [-0.025, 0.1], 0.046),
#             Mirror(mv([0.5, 0.08], it - 20), [0, -0.12], -0.44),
#             Mirror(mv([0.71, 0.9], it - 40), [0.06, 0.093], -0.35),
#             Mirror(mv([0.08, 0.4], it - 60), [0.1, 0.04], -0.35),
#             Mirror(mv([0.92, 0.4], it - 80), [-0.09, 0.04], -0.35)
#         ]
#         rayPos = [0.28, 0.95]
#         plt.imshow(createImage(rayPos, objects, 400, 5000))
        
#         plt.pause(0.05)
#         writer.grab_frame()

In [ ]:
# from matplotlib.animation import FFMpegWriter
# metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
# writer = FFMpegWriter(fps=15, metadata=metadata)

# fig = plt.figure()
# with writer.saving(fig, "animation3.mp4", dpi=200):
#     nf = 140
#     for it in range(nf):
#         if (it%10==0): print(it,end='')
#         print('.',end='')

#         n = 50
        
#         objects = [
#             Lens(mv([0.85, 0.15], it), [-0.1, 0.1], 0.046),
#             Lens(mv([0.8, 0.2], it - 20), [-0.05, 0.05], -0.06),
#             Mirror(mv([0.7, 0.35], it - 20), [0.05, 0], 0.06),
#             Mirror(mv([0.65, 0.3], it - 25), [0, 0.05], 0.06),
#             Mirror(mv([0.8, 0.45], it - 30), [0.05, 0], 0.06),
#             Mirror(mv([0.55, 0.2], it - 35), [0, 0.05], 0.06),
#             Lens(mv([0.55, 0.45], it - 45), [-0.15, 0.15], 0.1),
#             Lens(mv([0.4, 0.6], it - 65), [-0.15, 0.15], --0.09),
#             Mirror(mv([0.15, 0.85], it - 85), [-0.05, 0.05], --0.09),
#         ]
        
#         rayPos = [0.9, 0.1]
#         plt.imshow(createImage(rayPos, objects, 400, 5000))
        
#         plt.pause(0.05)
#         writer.grab_frame()